<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"></ul></div>

In [2]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import os,sys
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import SimpleITK as sitk
from scipy import ndimage as ndi
import skimage as skim
from skimage import feature
import pandas as pd
import xarray as xr
plt.rcParams['figure.figsize'] = (10,8)
import pickle as pkl
from mre import pytorch_unet_tb
from mre.prediction_v2 import MREDataset
from mre.plotting import torch_dl_vis, hv_dl_vis, hv_pred_comp
from tensorboardX import SummaryWriter
from torch.utils.data import Dataset, DataLoader
import torchvision.utils
from torchsummary import summary
import torch
import torch.nn as nn
from collections import defaultdict
import torch.nn.functional as F
import torch.optim as optim
from torch.optim import lr_scheduler
import time
import copy
import mre.prediction_v2 as pred
from mre.prediction_v2 import gen_LOO_models
from mre.prediction_v2 import add_LOO_predictions
from mre import train_model_full

import holoviews as hv
from holoviews import opts
hv.extension('bokeh')


# Load mre data
full_data_dir = '/pghbio/dbmi/batmanlab/Data/MRE/'
ds = pkl.load(open(full_data_dir+'mre_ds_preprocess_4_combomask.p', 'rb'))

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


ModuleNotFoundError: No module named 'robust_loss_pytorch'

In [ ]:
ds

In [2]:
a = {'one':1, 'two':2}
for i in a: print(i)

one
two


In [68]:
trans=True
clip=True
test_subj='331'

train_set = MREDataset(ds, set_type='train', transform = trans, clip=clip, test=test_subj)
val_set = MREDataset(ds, set_type='val', transform = trans, clip=clip, test=test_subj)
test_set = MREDataset(ds, set_type='test', transform = trans, clip=clip, test=test_subj, aug=False)

image_datasets = {
    'train': train_set, 'val': val_set, 'test':test_set
}

batch_size = 50

dataloaders = {
    'train': DataLoader(train_set, batch_size=batch_size, shuffle=False, sampler=torch.utils.data.sampler.RandomSampler(train_set, replacement=True, num_samples=200), num_workers=0),
    #'val': DataLoader(val_set, batch_size=batch_size, shuffle=False, sampler=torch.utils.data.sampler.RandomSampler(val_set, replacement=True, num_samples=100), num_workers=0),
    'val': DataLoader(val_set, batch_size=batch_size, shuffle=True, num_workers=0),
    'test': DataLoader(test_set, batch_size=batch_size, shuffle=False, num_workers=0)
}

dataset_sizes = {
    x: len(image_datasets[x]) for x in image_datasets.keys()
}

dataset_sizes

{'train': 140, 'val': 32, 'test': 4}

In [66]:
for i in dataloaders['train']:
    print(i[0].shape)

torch.Size([50, 3, 256, 256])
torch.Size([50, 3, 256, 256])
torch.Size([50, 3, 256, 256])
torch.Size([50, 3, 256, 256])


In [69]:
# Get a batch of training data
inputs, targets, masks, names = next(iter(dataloaders['test']))

#print(inputs.shape, masks.shape)
#for x in [inputs.numpy(), masks.numpy()]:
#    print(x.min(), x.max(), x.mean(), x.std())
print(inputs.shape)
print(targets.shape)
print(names)

#torch_dl_vis(inputs, targets, masks)
hv_dl_vis(inputs, targets, masks, names)

torch.Size([4, 3, 256, 256])
torch.Size([4, 1, 256, 256])
('331_0', '331_1', '331_2', '331_3')


Column
    [0] FloatSlider(end=1, name='mask', start=0, value=0.0)
    [1] Row
        [0] HoloViews(Layout)
        [1] Column
            [0] Select(name='subject', options=['331_0', '331_1', ...], value='331_0')

In [72]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

model = pytorch_unet_tb.UNet(1, cap=12)
model = model.to(device)

summary(model, input_size=(3, 256, 256))

cuda
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
         AddCoords-1          [-1, 5, 256, 256]               0
            Conv2d-2         [-1, 12, 256, 256]             552
         CoordConv-3         [-1, 12, 256, 256]               0
       BatchNorm2d-4         [-1, 12, 256, 256]              24
              ReLU-5         [-1, 12, 256, 256]               0
            Conv2d-6         [-1, 12, 256, 256]           1,308
       BatchNorm2d-7         [-1, 12, 256, 256]              24
              ReLU-8         [-1, 12, 256, 256]               0
         MaxPool2d-9         [-1, 12, 128, 128]               0
           Conv2d-10         [-1, 12, 128, 128]           1,308
      BatchNorm2d-11         [-1, 12, 128, 128]              24
             ReLU-12         [-1, 12, 128, 128]               0
           Conv2d-13         [-1, 12, 128, 128]           1,308
      BatchNorm2d-14         [-1, 

In [73]:
from datetime import datetime
now = datetime.today().strftime('%Y-%m-%d_%H-%M-%S')
print(now)

# Observe that all parameters are being optimized
optimizer_ft = optim.Adam(model.parameters(), lr=1e-2)

exp_lr_scheduler = pred.lr_scheduler.StepLR(optimizer_ft, step_size=20, gamma=0.1)

#writer = SummaryWriter('runs/baseline')
#writer = SummaryWriter('runs/clip_0')
#writer = SummaryWriter('runs/clip_norm_0')
#writer = SummaryWriter('runs/norm_redcap_0')
writer = SummaryWriter('runs/'+now)
model = pred.train_model(model, optimizer_ft, exp_lr_scheduler, device, dataloaders, num_epochs=60, tb_writer=writer)
#writer.export_scalars_to_json("./all_scalars.json")
writer.close()





2019-05-21_14-05-21
Epoch 0/59
----------
LR 0.01
train: loss: 164.909452
val: loss: 195.691895
saving best model
0m 7s
Epoch 1/59
----------
LR 0.01
train: loss: 165.020515
val: loss: 183.315567
saving best model
0m 6s
Epoch 2/59
----------
LR 0.01
train: loss: 151.254356
val: loss: 171.021332
saving best model
0m 5s
Epoch 3/59
----------
LR 0.01
train: loss: 165.996967
val: loss: 100.731247
saving best model
0m 6s
Epoch 4/59
----------
LR 0.01
train: loss: 146.779049
val: loss: 92.784325
saving best model
0m 6s
Epoch 5/59
----------
LR 0.01
train: loss: 149.130047
val: loss: 507.840973
0m 5s
Epoch 6/59
----------
LR 0.01
train: loss: 113.540125
val: loss: 420.348969
0m 6s
Epoch 7/59
----------
LR 0.01
train: loss: 115.747614
val: loss: 152.970993
0m 5s
Epoch 8/59
----------
LR 0.01
train: loss: 99.603495
val: loss: 124.831108
0m 5s
Epoch 9/59
----------
LR 0.01
train: loss: 91.439651
val: loss: 390.736572
0m 5s
Epoch 10/59
----------
LR 0.01
train: loss: 76.863337
val: loss: 863.4779

In [74]:
# prediction

import math

model.eval()   # Set model to evaluate mode

test_loader =  DataLoader(test_set, batch_size=4, shuffle=False, num_workers=0)
#test_loader = DataLoader(test_dataset, batch_size=3, shuffle=False, num_workers=0)
        
inputs, labels, masks, names = next(iter(test_loader))
inputs = inputs.to(device)
model_pred = model(inputs)
prediction_viz = hv_dl_vis(inputs, labels, masks, names, model_pred)
# labels = labels.to(device)

# model_pred = model(inputs)
# 
# model_pred_np = model_pred.data.cpu().numpy()
# labels = labels.data.cpu().numpy()
# inputs = inputs.data.cpu().numpy()
# masks = masks.data.cpu().numpy()
# print(inputs.shape)

# Change channel-order and make 3 channels for matplot
#input_images_rgb = [reverse_transform(x) for x in inputs.cpu()]

# Map each channel (i.e. class) to each color
#target_masks_rgb = [helper.masks_to_colorimg(x) for x in labels.cpu().numpy()]
#pred_rgb = [helper.masks_to_colorimg(x) for x in pred]

#helper.plot_side_by_side([input_images_rgb, target_masks_rgb, pred_rgb])

In [75]:
#pred_layout = hv.Layout(prediction_viz[1][0])
#hv.save(prediction_viz[1][0], 'prediction_example.png')
prediction_viz

Column
    [0] FloatSlider(end=1, name='mask', start=0, value=0.0)
    [1] Row
        [0] HoloViews(Layout)
        [1] Column
            [0] Select(name='subject', options=['331_0', '331_1', ...], value='331_0')

In [77]:
gen_LOO_models(ds, full_data_dir, cap=12, verbose=False)

2019-05-21_14-17-38


In [79]:
test_ds = add_LOO_predictions(ds, full_data_dir, version='2019-05-21_14-17-38')

In [80]:
pkl.dump(test_ds, open(full_data_dir+'mre_ds_preprocess_5_pred_v2.p', 'wb'), protocol=-1)

In [66]:
hv.save(layout, 'filter_examples.png')